### 参考:

https://blog.csdn.net/weixin_35154281/article/details/112493756

In [95]:
import pandas as pd
#from deepctr.feature_column import SparseFeat, VarLenSparseFeat
from sklearn.preprocessing import LabelEncoder

import random
import numpy as np
from tqdm import tqdm
#from tensorflow.python.keras.preprocessing.sequence import pad_sequences
#from deepmatch.models import *
#from deepmatch.utils import sampledsoftmaxloss


import warnings
warnings.filterwarnings("ignore")

In [96]:
x = [1,3,4,4,5,5]
print(x[::-1])

[5, 5, 4, 4, 3, 1]


In [97]:
path='./ml-1m/'
unames = ['user_id', 'gender', 'age', 'occupation', 'zip']
rnames = ['user_id', 'movie_id', 'rating', 'timestamp']
mnames = ['movie_id', 'title', 'genres']

users = pd.read_csv(path+'users.dat', sep='::', header=None, names=unames,engine='python',encoding='ISO-8859-1')
ratings = pd.read_table(path+'ratings.dat', sep='::', header=None, names=rnames, engine='python')
movies = pd.read_table(path+'movies.dat', sep='::', header=None, names=mnames, engine='python',encoding='ISO-8859-1')
#encoding='ISO-8859-1'
#解决‘utf-8‘ codec can‘t decode byte 0xe9 in position 3114: invalid continuation byte 错误

data = pd.merge(pd.merge(ratings, users, on='user_id'), movies, on='movie_id').sample(20000)
data.info



<bound method DataFrame.info of         user_id  movie_id  rating   timestamp gender  age  occupation    zip  \
322629     5511       357       4   959788018      M   45           1  92407   
626738     5265      1179       4   961220813      M   45           1  97405   
156027     1651      1090       2  1002181287      M   25          12  94520   
108535     2546      2858       4   974040685      F   56          13  37931   
843613     2947      1172       5  1037739292      F   25           0  02138   
...         ...       ...     ...         ...    ...  ...         ...    ...   
481519     5805      3489       2   958107420      F   25           0  90802   
292182     3931      3113       3   965708030      M   25           5  92117   
310831     3069      1093       5   969952034      M   18           4  97470   
614884     5269       628       4   961166900      M   18           0  37211   
887375     5976      1190       4   956946207      F   25           1  26542   

       

In [61]:
data.head()

user_id  movie_id  rating  timestamp gender  age  occupation    zip  \
522081     5070       539       3  963382596      M   25           2  55344   
254219      915       377       3  975203781      M   25           7  72762   
683253     3158      1591       2  968884562      M   25          15  15217   
877183     5227      1752       2  961475757      M   18          10  64050   
806865     1288      2065       3  974793866      F   35          19  92867   

                                   title                            genres  
522081       Sleepless in Seattle (1993)                    Comedy|Romance  
254219                      Speed (1994)           Action|Romance|Thriller  
683253                      Spawn (1997)  Action|Adventure|Sci-Fi|Thriller  
877183                  Hard Rain (1998)                   Action|Thriller  
806865  Purple Rose of Cairo, The (1985)              Comedy|Drama|Romance

In [62]:
sparse_features = ["movie_id", "user_id",
                    "gender", "age", "occupation", "zip", ]
SEQ_LEN = 50
negsample = 3

In [63]:
features = ['user_id', 'movie_id', 'gender', 'age', 'occupation', 'zip']

feature_max_idx = {}
for feature in features:
    lbe = LabelEncoder()
    data[feature] = lbe.fit_transform(data[feature]) + 1  # 默认编码从０开始
    feature_max_idx[feature] = data[feature].max() + 1  # 作为Embedding向量的大小设定

In [64]:
# 构建用户画像
user_profile = data[["user_id", "gender", "age", "occupation", "zip"]].drop_duplicates('user_id')
user_profile.set_index("user_id", inplace=True)
user_profile


gender  age  occupation   zip
user_id                               
3926          2    3           3  1534
723           2    3           8  1881
2439          2    3          16   521
4043          2    2          11  1781
1015          1    4          20  2479
...         ...  ...         ...   ...
3469          2    4           8   836
698           1    4          15  2460
626           1    6           8   640
4323          2    5           2  1391
1133          1    3           5  2332

[4685 rows x 4 columns]

In [65]:
# 构建物品画像
item_profile = data[["movie_id"]].drop_duplicates('movie_id')
item_profile.head()

movie_id
522081       422
254219       296
683253      1069
877183      1175
806865      1387

In [66]:
# 用户历史点击文章序列
user_item_list = data.groupby("user_id")['movie_id'].apply(list)
user_item_list

user_id
1                                            [1256, 1945]
2                                            [1534, 1051]
3                                              [990, 869]
4                                                  [2550]
5                            [2268, 245, 1043, 1245, 396]
                              ...                        
4681           [1643, 1158, 113, 2206, 745, 20, 330, 319]
4682    [841, 477, 2052, 1757, 1237, 1380, 2385, 1587,...
4683                        [733, 1751, 2015, 1257, 1387]
4684                                    [2097, 643, 1483]
4685               [1600, 1563, 812, 2551, 949, 872, 616]
Name: movie_id, Length: 4685, dtype: object

In [67]:
data.sort_values("timestamp", inplace=True)
item_ids = data['movie_id'].unique()
negsample=3



In [68]:
item_ids

array([1483, 2097,  643, ..., 1275, 2649, 2471], dtype=int64)

In [69]:
data

user_id  movie_id  rating   timestamp  gender  age  occupation   zip  \
473027     4684      1483       3   956705636       1    5           1    11   
807598     4684      2097       3   956705749       1    5           1    11   
638417     4684       643       4   956706201       1    5           1    11   
922867     4682      1851       3   956709631       1    3          16   937   
182196     4682       846       4   956710871       1    3          16   937   
...         ...       ...     ...         ...     ...  ...         ...   ...   
503134     2613      1979       5  1046120162       2    2           5  1303   
995542     2613       999       4  1046188535       2    2           5  1303   
770954     2613      2488       4  1046188847       2    2           5  1303   
822206     2613       688       3  1046199406       2    2           5  1303   
446982     1243       877       5  1046275969       2    3          13   316   

                                  title                   genres  
473027               Beetlejuice (1988)           Comedy|Fantasy  
807598  Taming of the Shrew, The (1967)                   Comedy  
638417                     Laura (1944)  Crime|Film-Noir|Mystery  
922867               Desert Blue (1999)                    Drama  
182196             Graduate, The (1967)            Drama|Romance  
...                                 ...                      ...  
503134       Hard Day's Night, A (1964)           Comedy|Musical  
995542                Gridlock'd (1997)                    Crime  
770954        Honeymoon in Vegas (1992)           Comedy|Romance  
822206     Swiss Family Robinson (1960)     Adventure|Children's  
446982        Young Frankenstein (1974)            Comedy|Horror  

[20000 rows x 10 columns]

In [86]:
group = data.groupby('user_id')
for reviewerID, hist in data.groupby('user_id'):
    print(reviewerID)
    print(hist)

1
       user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
8926         1      1945       5  978300719       1    1          11  1282   
36324        1      1256       4  978824330       1    1          11  1282   

                           title                genres  
8926   Christmas Story, A (1983)          Comedy|Drama  
36324               Mulan (1998)  Animation|Children's  
2
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
64571         2      1534       5  978299297       2    7          17  1850   
131343        2      1051       3  978299941       2    7          17  1850   

                         title                     genres  
64571   Few Good Men, A (1992)                Crime|Drama  
131343          Con Air (1997)  Action|Adventure|Thriller  
3
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
187684        3       990       3  978297095       2    3          16  1511   
23271       

401624  Romeo Must Die (2000)  Action|Romance  
129
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
239679      129      1866       4  977199259       2    3           8  1575   
528399      129      1346       4  977200615       2    3           8  1575   
566095      129       558       2  977205782       2    3           8  1575   
439590      129       458       5  977210208       2    3           8  1575   

                                              title  \
239679  South Park: Bigger, Longer and Uncut (1999)   
528399           Back to the Future Part III (1990)   
566095                  Nutty Professor, The (1996)   
439590                                Batman (1989)   

                               genres  
239679               Animation|Comedy  
528399          Comedy|Sci-Fi|Western  
566095  Comedy|Fantasy|Romance|Sci-Fi  
439590   Action|Adventure|Crime|Drama  
130
        user_id  movie_id  rating  timestamp  gender  age  occupation   

974930                      Face in the Crowd, A (1957)         Drama  
253
      user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
8991      253      1945       3  976396015       2    4          13  2106   

                          title        genres  
8991  Christmas Story, A (1983)  Comedy|Drama  
254
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
416188      254      2701       4  976393100       2    4           8   71   
38047       254      1912       5  976393294       2    4           8   71   
41736       254         1       3  976393427       2    4           8   71   
160023      254       353       4  976393542       2    4           8   71   
68387       254      2016       3  976393560       2    4           8   71   
396103      254      2423       2  976393914       2    4           8   71   
100669      254      2392       4  976394253       2    4           8   71   
36349       254      1256       3  976472778 

236801            Piano, The (1993)      Drama|Romance  
386
       user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
22865      386       523       5  976643934       1    2           3  1501   

                                                   title     genres  
22865  Wallace & Gromit: The Best of Aardman Animatio...  Animation  
387
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
809929      387      1315       2  976226454       2    3           3  537   
845973      387      2554       5  976311162       2    3           3  537   

                                    title                      genres  
809929  Friday the 13th Part 3: 3D (1982)                      Horror  
845973                 Angel Heart (1987)  Film-Noir|Mystery|Thriller  
388
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
478898      388      1958       4  976209179       2    4          18  1054   

                        

931862                         On the Town (1949)                Musical  
517
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
564223      517      1796       3  975695042       1    6          14  1017   
144364      517      1646       5  975695150       1    6          14  1017   
359231      517      1868       4  975695197       1    6          14  1017   

                             title          genres  
564223          Pushing Tin (1999)          Comedy  
144364  Shakespeare in Love (1998)  Comedy|Romance  
359231        Summer of Sam (1999)           Drama  
518
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
724139      518      1934       4  975691938       1    3           1  330   

                                 title  genres  
724139  Airplane II: The Sequel (1982)  Comedy  
519
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
746747      519      1660       3  975690510       

...

613136  Jakob the Liar (1999)  Drama  
4045
       user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
73204     4045       812       3  961545894       2    3          13  2330   

                                                   title  \
73204  Star Wars: Episode VI - Return of the Jedi (1983)   

                                    genres  
73204  Action|Adventure|Romance|Sci-Fi|War  
4046
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
461911     4046      2105       3  961460633       2    4           8  2438   

                        title                genres  
461911  Little Big Man (1970)  Comedy|Drama|Western  
4047
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
324977     4047      1656       4  961458303       2    3           5  494   
547867     4047      1363       2  961459244       2    3           5  494   

                             title                           genres  
324977

650274  Dark City (1998)  Film-Noir|Sci-Fi|Thriller  
4176
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
55201      4176       415       5  960260504       1    2           2  619   
379075     4176       258       5  960260594       1    2           2  619   
154759     4176        20       3  960260765       1    2           2  619   
364353     4176       175       4  960261049       1    2           2  619   

                                     title               genres  
55201            Secret Garden, The (1993)     Children's|Drama  
379075  What's Eating Gilbert Grape (1993)                Drama  
154759                   Get Shorty (1995)  Action|Comedy|Drama  
364353            Dolores Claiborne (1994)       Drama|Thriller  
4177
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
111649     4177       827       4  960258269       1    3           1  874   
897419     4177      1289       4  960258299       1    3  

840270  American Gigolo (1980)   Drama  
4308
        user_id  movie_id  rating   timestamp  gender  age  occupation  zip  \
409457     4308      1564       4  1000932087       2    2          18   70   

                         title  genres  
409457  My Cousin Vinny (1992)  Comedy  
4309
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
553364     4309      1368       3  959350082       2    4           8  670   
113921     4309       201       4  959351034       2    4           8  670   
73355      4309       812       2  959351625       2    4           8  670   
464795     4309       607       5  959352166       2    4           8  670   

                                                    title  \
553364             Computer Wore Tennis Shoes, The (1970)   
113921  Like Water for Chocolate (Como agua para choco...   
73355   Star Wars: Episode VI - Return of the Jedi (1983)   
464795                                 Rear Window (1954)   

           

257241             Faculty, The (1998)  Horror|Sci-Fi  
4440
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
740270     4440        11       4  958441889       2    2           1  2537   

                                 title                genres  
740270  American President, The (1995)  Comedy|Drama|Romance  
4441
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
353714     4441       823       5  958438367       1    3          12  331   
439466     4441      1824       4  958869579       1    3          12  331   

                                 title                   genres  
353714  Godfather: Part II, The (1974)       Action|Crime|Drama  
439466                 Superman (1978)  Action|Adventure|Sci-Fi  
4442
        user_id  movie_id  rating  timestamp  gender  age  occupation  zip  \
493438     4442      1655       4  958434162       1    3          12   68   
343657     4442       615       5  958434230       1   

262481            Player, The (1992)                Comedy|Drama  
4567
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
76017      4567       815       5  957468420       2    4          21  1970   
577598     4567       861       4  957468917       2    4          21  1970   
45666      4567      1301       2  957469139       2    4          21  1970   
954254     4567      1982       4  957469766       2    4          21  1970   

                                title         genres  
76017               GoodFellas (1990)    Crime|Drama  
577598       Great Escape, The (1963)  Adventure|War  
45666       Driving Miss Daisy (1989)          Drama  
954254  Buddy Holly Story, The (1978)          Drama  
4568
        user_id  movie_id  rating  timestamp  gender  age  occupation   zip  \
592240     4568      1720       2  957467827       2    2           5  1544   
621835     4568      1258       2  981678009       2    2           5  1544   

              

In [87]:
def gen_data_set(data, negsample=3):

    data.sort_values("timestamp", inplace=True)
    item_ids = data['movie_id'].unique()

    train_set = []
    test_set = []
    for reviewerID, hist in tqdm(data.groupby('user_id')):
        pos_list = hist['movie_id'].tolist()
        rating_list = hist['rating'].tolist()

        if negsample > 0:
            candidate_set = list(set(item_ids) - set(pos_list))
            neg_list = np.random.choice(candidate_set,size=len(pos_list)*negsample,replace=True)
        for i in range(1, len(pos_list)):
            hist = pos_list[:i]
            if i != len(pos_list) - 1:
                train_set.append((reviewerID, hist[::-1], pos_list[i], 1, len(hist[::-1]),rating_list[i]))
                for negi in range(negsample):
                    train_set.append((reviewerID, hist[::-1], neg_list[i*negsample+negi], 0,len(hist[::-1])))
            else:
                test_set.append((reviewerID, hist[::-1], pos_list[i],1,len(hist[::-1]),rating_list[i]))

    #random.shuffle(train_set)
    #random.shuffle(test_set)

    print(len(train_set[0]),len(test_set[0]))

    return train_set,test_set

In [88]:
train_set, test_set = gen_data_set(data, negsample)

100%|████████████████████████████████████████████████████████████████████████████| 4685/4685 [00:01<00:00, 2976.12it/s]

6 6


In [89]:
train_set

[(5, [2268], 1043, 1, 1, 4),
 (5, [2268], 1033, 0, 1),
 (5, [2268], 160, 0, 1),
 (5, [2268], 375, 0, 1),
 (5, [1043, 2268], 396, 1, 2, 4),
 (5, [1043, 2268], 2353, 0, 2),
 (5, [1043, 2268], 2659, 0, 2),
 (5, [1043, 2268], 2334, 0, 2),
 (5, [396, 1043, 2268], 245, 1, 3, 3),
 (5, [396, 1043, 2268], 1881, 0, 3),
 (5, [396, 1043, 2268], 2058, 0, 3),
 (5, [396, 1043, 2268], 1331, 0, 3),
 (7, [1368], 1338, 1, 1, 4),
 (7, [1368], 757, 0, 1),
 (7, [1368], 320, 0, 1),
 (7, [1368], 2189, 0, 1),
 (7, [1338, 1368], 1655, 1, 2, 4),
 (7, [1338, 1368], 828, 0, 2),
 (7, [1338, 1368], 1543, 0, 2),
 (7, [1338, 1368], 1253, 0, 2),
 (7, [1655, 1338, 1368], 1389, 1, 3, 3),
 (7, [1655, 1338, 1368], 2255, 0, 3),
 (7, [1655, 1338, 1368], 457, 0, 3),
 (7, [1655, 1338, 1368], 1236, 0, 3),
 (11, [1336], 1268, 1, 1, 4),
 (11, [1336], 2577, 0, 1),
 (11, [1336], 1715, 0, 1),
 (11, [1336], 1071, 0, 1),
 (11, [1268, 1336], 459, 1, 2, 4),
 (11, [1268, 1336], 1756, 0, 2),
 (11, [1268, 1336], 1273, 0, 2),
 (11, [1268, 1

In [90]:
test_set

[(1, [1945], 1256, 1, 1, 4),
 (2, [1534], 1051, 1, 1, 3),
 (3, [990], 869, 1, 1, 3),
 (5, [245, 396, 1043, 2268], 1245, 1, 4, 3),
 (6, [119], 1134, 1, 1, 5),
 (7, [1389, 1655, 1338, 1368], 197, 1, 4, 5),
 (11, [459, 1268, 1336], 2385, 1, 3, 4),
 (12, [2648, 2435, 1797, 1362], 2505, 1, 4, 2),
 (13, [1348, 44, 1654, 362, 803, 287], 71, 1, 6, 3),
 (14, [1414, 1, 890, 2506], 864, 1, 4, 4),
 (16, [437, 1643, 1665, 1452], 1345, 1, 4, 4),
 (17, [1912, 11, 497, 240, 766, 627, 1386, 329], 2059, 1, 8, 3),
 (18, [252, 469, 1122, 1483, 906], 1817, 1, 5, 3),
 (19, [2068], 798, 1, 1, 5),
 (20,
  [2248, 2260, 786, 790, 1111, 2291, 2660, 544, 2434, 1142, 258],
  1529,
  1,
  11,
  5),
 (22, [488, 1781, 846], 978, 1, 3, 4),
 (23, [812, 770], 119, 1, 2, 2),
 (24, [749], 2721, 1, 1, 4),
 (26, [740, 1343, 589, 2169], 1284, 1, 4, 3),
 (27, [260, 1663, 1329], 1017, 1, 3, 4),
 (28, [2393, 2548], 875, 1, 2, 3),
 (29, [864, 1680, 967, 1656, 1975], 368, 1, 5, 5),
 (31, [1057], 1, 1, 1, 5),
 (32, [1386, 1483, 6,

In [80]:
def gen_model_input(train_set,user_profile,seq_max_len):

    train_uid = np.array([line[0] for line in train_set])
    train_seq = [line[1] for line in train_set]
    train_iid = np.array([line[2] for line in train_set])
    train_label = np.array([line[3] for line in train_set])
    train_hist_len = np.array([line[4] for line in train_set])
    
    # 填补缺失值
    train_seq_pad = pad_sequences(train_seq, maxlen=seq_max_len, padding='post', truncating='post', value=0)
    
    # 标签　movie_id:最后一次的点击视频id号
    train_model_input = {"user_id": train_uid, "movie_id": train_iid, "hist_movie_id": train_seq_pad,
                         "hist_len": train_hist_len}
    
    # 添加用户信息
    for key in ["gender", "age", "occupation", "zip"]:
        train_model_input[key] = user_profile.loc[train_model_input['user_id']][key].values

    return train_model_input, train_label

In [81]:
train_set, test_set = gen_data_set(data, negsample)
#train_model_input, train_label = gen_model_input(train_set, user_profile, SEQ_LEN)
#test_model_input, test_label = gen_model_input(test_set, user_profile, SEQ_LEN)

100%|████████████████████████████████████████████████████████████████████████████| 4685/4685 [00:01<00:00, 2979.07it/s]

6 6


In [41]:
embedding_dim = 16
user_feature_columns = [SparseFeat('user_id', feature_max_idx['user_id'], embedding_dim),
                        SparseFeat("gender", feature_max_idx['gender'], embedding_dim),
                        SparseFeat("age", feature_max_idx['age'], embedding_dim),
                        SparseFeat("occupation", feature_max_idx['occupation'], embedding_dim),
                        SparseFeat("zip", feature_max_idx['zip'], embedding_dim),
                        VarLenSparseFeat(SparseFeat('hist_movie_id', feature_max_idx['movie_id'], embedding_dim,
                                                    embedding_name="movie_id"), SEQ_LEN, 'mean', 'hist_len'),
                        ]


item_feature_columns = [SparseFeat('movie_id', feature_max_idx['movie_id'], embedding_dim)]

NameError: name 'SparseFeat' is not defined